In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
#read the data
import pandas as pd
data = pd.read_csv("/content/drive/Shareddrives/2:1 Caitlin & Kimai/Data/Enzyme Stability Prediction/preprocessed.csv")
data.head()

feature 1  feature 2  feature 3  feature 4  feature 5  feature 6  \
0     13.196      7.331      1.466      3.812      0.293      8.798   
1      9.790     10.490      2.098      3.497      0.000     18.182   
2     10.060      6.237      3.018      5.433      1.811      6.439   
3      7.547      3.774      3.396      7.170      1.887     10.943   
4      5.927      4.342      4.480      5.376      0.965      5.376   

   feature 7  feature 8  feature 9  feature 10  ...   M   N    P   Q   R    S  \
0      1.760     11.144      0.880       4.106  ...   8   5   18   6  25   11   
1      7.692      6.294      1.399       4.545  ...   2   6    8  22  30   14   
2      5.030     13.078      2.213       3.219  ...   6  15   20  25  31   33   
3      3.396      6.038      2.642       3.774  ...   2   9   16   9  10   16   
4      3.722      5.789      2.757       4.893  ...  31  65  128  54  63  148   

     T    V   W   Y  
0   14   37   4   3  
1   12   13   3   3  
2   30   30   3  16  
3   19   14   3   4  
4  120  124  16  47  

[5 rows x 49 columns]

In [3]:
#Check the columns
data.columns

Index(['feature 1', 'feature 2', 'feature 3', 'feature 4', 'feature 5',
       'feature 6', 'feature 7', 'feature 8', 'feature 9', 'feature 10',
       'feature 11', 'feature 12', 'feature 13', 'feature 14', 'feature 15',
       'feature 16', 'feature 17', 'feature 18', 'feature 19', 'feature 20',
       'pH', 'tm', 'molecular_weight', 'gravy', 'aromaticity',
       'isoelectric_point', 'helix', 'turn', 'sheet', 'A', 'C', 'D', 'E', 'F',
       'G', 'H', 'I', 'K', 'L', 'M', 'N', 'P', 'Q', 'R', 'S', 'T', 'V', 'W',
       'Y'],
      dtype='object')

In [4]:
from sklearn.model_selection import train_test_split

#splitting
X = data.drop('tm', axis = 1)
Y = data['tm']

x_train, x_test, y_train, y_test = train_test_split(X, Y, test_size = 0.2, random_state = 42)
print("Train shape", x_train.shape)
print("Test shape", x_test.shape)

Train shape (23184, 48)
Test shape (5797, 48)


### Decision Tree

In [5]:
from sklearn.tree import DecisionTreeRegressor
from sklearn.metrics import mean_squared_error
import numpy as np

dct = DecisionTreeRegressor()
dct.fit(x_train, y_train)

#predictions
y_pred = dct.predict(x_test)

rmse = np.sqrt(mean_squared_error(y_test, y_pred))
print("Root mean squared value", rmse)

Root mean squared value 11.360618366411321


### Getting predictions from the navigator

In [6]:
import requests
import json
def get_prediction(data):
  url = "https://askai.aiclub.world/2888bd56-f1bf-42c9-a2a5-f6ac8f805543"
  r = requests.post(url, data=json.dumps(data))
  response = getattr(r,"content").decode("utf-8")
  print(response)
  return response

In [7]:
#call the test data
test_data = pd.read_csv("/content/drive/Shareddrives/2:1 Caitlin & Kimai/Data/Enzyme Stability Prediction/test_data.csv")
test_data.head()

feature 1  feature 2  feature 3  feature 4  feature 5  feature 6  \
0      9.955      1.357      8.597      6.787      1.810      3.620   
1      9.955      1.357      8.597      6.787      1.810      3.167   
2     10.000      1.364      8.636      6.818      1.818      3.182   
3      9.955      1.357      8.597      6.787      2.262      3.167   
4      9.955      1.357      8.597      6.787      1.810      3.167   

   feature 7  feature 8  feature 9  feature 10  ...   N   P   Q  R   S  T   V  \
0      5.882      8.597        0.0       2.715  ...  19  17  13  3  18  8  13   
1      5.882      8.597        0.0       2.715  ...  19  17  13  3  18  8  13   
2      5.909      8.636        0.0       2.727  ...  19  17  13  3  18  8  13   
3      5.882      8.597        0.0       2.715  ...  19  17  13  3  18  8  13   
4      5.882      8.597        0.0       2.715  ...  19  17  13  3  18  8  13   

   W  Y  seq_id  
0  6  6   31390  
1  6  6   31391  
2  6  6   31392  
3  6  6   31393  
4  6  6   31394  

[5 rows x 49 columns]

In [8]:
#creating a copy
df = test_data.copy()

In [9]:
#shape
df.shape

(2413, 49)

In [10]:
#drop the seq id
df.drop('seq_id', axis = 1, inplace = True)

In [11]:
#get the predictions
data_records = df.to_dict("records")

predictions = []

for index,record in enumerate(data_records):
  print(index)
  response = get_prediction(record)
  response = json.loads(response)
  response = json.loads(response['body'])
  prediction = response['predicted_label']
  predictions.append(prediction)

0
{"statusCode": 200, "body": "{\"predicted_label\": 38.36, \"Insight\": {\"featureImportance\": {\"format\": \"table\", \"name\": \"Feature Importance\", \"headers\": [\"Feature\", \"Value\"], \"data\": [{\"Feature\": \"feature 3\", \"Value\": 0.10343934669855578}, {\"Feature\": \"feature 7\", \"Value\": 0.08960244101016154}, {\"Feature\": \"feature 16\", \"Value\": 0.08306846275535902}, {\"Feature\": \"sheet\", \"Value\": 0.0766139880456119}, {\"Feature\": \"pH\", \"Value\": 0.062303549814132345}, {\"Feature\": \"feature 12\", \"Value\": 0.04751148499546683}, {\"Feature\": \"feature 10\", \"Value\": 0.04508348326295287}, {\"Feature\": \"feature 1\", \"Value\": 0.033428164455552564}, {\"Feature\": \"feature 13\", \"Value\": 0.029461849669501224}, {\"Feature\": \"feature 2\", \"Value\": 0.02768279200468332}, {\"Feature\": \"feature 5\", \"Value\": 0.023921056096497726}, {\"Feature\": \"feature 4\", \"Value\": 0.019595341347810102}, {\"Feature\": \"feature 19\", \"Value\": 0.01870768853

In [12]:
#attch the predictions to the main dataframe
test_data['tm'] = predictions
submission = test_data[['seq_id','tm']]
submission.head()

seq_id     tm
0   31390  38.36
1   31391  39.13
2   31392  38.36
3   31393  38.36
4   31394  38.36

In [13]:
submission.to_csv("submission.csv", index = False)